In [22]:
import time, re
from collections import Counter
import numpy as np

Mycket av koden är hämtat från https://github.com/udacity/deep-learning/tree/master/embeddings 

In [225]:
PATH = 'data/'
!ls data

ahnflefn.txt dec1980.txt  dec2000.txt


In [226]:
%%time
with open(f'{PATH}dec2000.txt') as f:
    text = f.read()

CPU times: user 3.03 s, sys: 1.75 s, total: 4.78 s
Wall time: 4.79 s


In [139]:
# Begränsa textstorleken
text = text[:1000000]

## Preprocessing

Here I'm fixing up the text to make training easier. This comes from the `utils` module I wrote. The `preprocess` function coverts any punctuation into tokens, so a period is changed to ` <PERIOD> `. In this data set, there aren't any periods, but it will help in other NLP problems. I'm also removing all words that show up five or fewer times in the dataset. This will greatly reduce issues due to noise in the data and improve the quality of the vector representations. If you want to write your own functions for this stuff, go for it.

In [227]:
def preprocess(text):

    # Replace punctuation with tokens so we can use them in our model
    text = text.lower()
    text = text.replace('.', ' <PERIOD> ')
    text = text.replace(',', ' <COMMA> ')
    text = text.replace('"', ' <QUOTATION_MARK> ')
    text = text.replace(';', ' <SEMICOLON> ')
    text = text.replace('!', ' <EXCLAMATION_MARK> ')
    text = text.replace('?', ' <QUESTION_MARK> ')
    text = text.replace('(', ' <LEFT_PAREN> ')
    text = text.replace(')', ' <RIGHT_PAREN> ')
    text = text.replace('--', ' <HYPHENS> ')
    text = text.replace('?', ' <QUESTION_MARK> ')
    text = text.replace('-\n', '')
    text = text.replace(':', ' <COLON> ')
    words = text.split()
    
    # Remove all words with  5 or fewer occurences
    #word_counts = Counter(words)
    #trimmed_words = [word for word in words if word_counts[word] > 5]
    trimmed_words = words
    return trimmed_words

In [228]:
%%time 
#CPU times: user 48.3 s, sys: 7.27 s, total: 55.6 s
words = preprocess(text)
print(words[:30])

['\ufefftill', 'statsrådet', 'och', 'chefen', 'för', 'utrikesdepartementet', 'regeringen', 'bemyndigade', 'genom', 'beslut', 'den', '18', 'oktober', '2001', 'chefen', 'för', 'utrikesdepartementet', 'att', 'tillkalla', 'en', 'kommission', 'med', 'uppgift', 'att', 'utreda', 'och', 'värdera', 'hur', 'den', 'svenska']
CPU times: user 23.6 s, sys: 11.2 s, total: 34.8 s
Wall time: 36.2 s


In [229]:
print("Total words: {}".format(len(words)))
print("Unique words: {}".format(len(set(words))))

Total words: 107910403
Unique words: 974524


## Make chunks

In [146]:
len(words)

56107

In [230]:
def make_chunks (words, chunk_size):
    num_chunks = len(words)//chunk_size
    return [x * chunk_size for x in range (num_chunks)]
    

## Kapitel

In [231]:
def make_freq (words):
    counter = Counter(words)
    sum_of = sum(counter.values())
    return {x:(counter[x]/sum_of) for x in counter}

In [232]:
def compare_freqs (sub_dict, total_dict):
    return {word:(sub_dict[word]/total_dict[word]) for word in sub_dict}
    

## Kapitel

In [233]:
def characteristic_words(words, chunk_size):
    freq_total = make_freq(words)
    start_at = make_chunks(words, chunk_size)
    for x in start_at:
        words_sub = words[x: x+chunk_size]
        freq_sub = make_freq(words_sub)
        comp_freqs = compare_freqs(freq_sub, freq_total)
        list1 = sorted(comp_freqs, key=comp_freqs.get, reverse=True)
        print (list1[:10], '\n')
    return comp_freqs
        

In [30]:
# Korta ner texten?
words = words[:1000000]

In [234]:
%%time
x = characteristic_words(words, 5000)

['törnudd', 'uppdragstid', 'ulfving', '1944–1945', 'pilkorsväldet', 'störningsfaktorer', 'problemformuleringsfasen', 'isande', 'kronvall', 'grata'] 

['uppmarsch-områden', 'förhandlingsspråk', 'ingermanländska', 'offensivens', 'lászló', 'ud-personalens', 'andrássy', 'sulners', 'meiers', 'samtalsrapporter'] 

['feller/meier', 'nivåproblemet', '1947-51', '1947–51', '1965–78', "'påminna'", '1952–55', 'engfeldts', 'sovjetledningens', 'förhandlingskultur'] 

['tärmyndigheter', 'bukarestbeskick-', 'utrikeskommissaria-', 'bukarestlegationens', 'informa19', 'rödakorsrepresentanten', 'kossuthradion', 'frå21', 'offi24', 'svenskt-'] 

['dership', "leadership's", "army's", 'encirclement', 'disorientation', "söderblom's", 'brusquely', 'soviet-controlled', 'mid-march', "ministry's"] 

['oppositionsledarna', 'archivist', 'arkivare', 'krigsarkivare', 'arkivstud-', 'nyckeltjänste-', 'rikespolitisk', 'störningsfaktorerna', 'standardförfarandena', 'typologiseras'] 

['personalbesättning', '25/4-1945]', '

['skottssituationer', 'räkenskapsfel', 'ekonomiansvarige', '7090-06', 'förvalningslagsutredningens', 'regeringsrättspraxis', 'skattetilläggsbestämmelsers', 'inkomsttaxerings-', 'förarbets545', 'kontrollaktion'] 

['skattebedrägeri-', 'skönsbeskattade', 'skönstaxerings-', 'sanktionsbehovet', '60619/00', 'skönstaxerades', 'rosenquists', '4902-07', '9631/04', 'zolotukhin'] 

['zolotukhin-', 'tullrätts-', '574\ufeff6', 'huvud189', 'sporandiskt', 'estetisk-kulturella', 'carlberg-målet', '8133-08', 'skönstaxeringsspekulera', 'skattetilläggssynpunkt'] 

['del192', 'förstagångsdeltagare', 'grannar/vänner', 'gemenskapsmotivet', 'kurstyperna', 'kunskapslyfter', 'deltagarkollektivet', 'folkhögskolebakgrund', 'studiecirkeldeltagares', 'forskningsintervjuer'] 

['ledarna/lärarna', 'omtugg', 'studiekontexten', 'vardagskontext', 'landströms', 'bildaridentitet', 'bortdefiniera', 'distansformens', 'föreningsåtaganden', 'stressriskerna'] 

['u-landsfrågor', 'varåt', 'meningsinnehållet', 'identitetsberät


['ingripandeformar', 'sven-göran', '2005/5/11', 'kasinomiljöer', 'faktorer1', 'spegelpopulation', 'kru11', 'skattekriminalitet', 'kasinoutvärderingens', 'jämförelsepopulations'] 

['legitimimera', 'spelmarknaderna', 'sharking', 'gär124', 'kasinospelarna', 'årsinkomstgruppen', 'seminariedeltagarna2', 'besöksfördelningen', 'doleys', 'besöksfrekvensgrupp'] 

['innekretsar', 'kutrapport', 'statusmeriterande', 'lilley', 'dutton', 'bankliknande', 'penningtvättare', 'narkotikalangare', 'kasinofallet', 'rouletten'] 

['påföljd15', 'besök16', 'regressionsanalys17', 'överrepresenta17', 'riskpopulationer', '80tal', 'flergångs18', '10020', '10021', '10022'] 

['kontantmängder', 'duyne', 'pengasummor', 'under165', 'kasinogruppen', 'jämförelsepopulationer', 'metodtriangulering', 'fifflarens', 'personlighetsdragets', 'branschkodning'] 

['[62]\ufeffförord', 'växtekolog', 'rapportsammanställning', 'ansvarskommittéerna', 'folkmängdsförändringar', 'vardagslivsperspektiv', 'munikationernas', 'klaesson',

['företagsledar-', 'aktiekursmaximering', 'kvartalskapitalism', 'nance-utvecklingen', 'spar203', 'kursmaximerande', 'tagsledningar', 'fallskärmsavtalen', 'månsbaserad', 'haussat'] 

['snabbutbilda', 'mandatåret', 'styrelsernas/företagsledningarnas', 'ägargrupperingar', 'ordföranderoll', 'mofråga', 'beslutsfråga', 'styrelserepresenation', 'förtroendekritisk', 'sysslomannarollen'] 

['röstningslokalerna', 'fastighetsbildningsåtgärder', 'folkomröstningslagen', 'budröstning', '1994–2004', 'röstningsförfaranden', '1650', 'e-röstning', 'brevröstningen', 'kandidatur'] 

['93/106/eg', 'röstmottaggarna', 'valkretsbeteck-', 'listtypbeteckning', 'bildningsåtgärder', 'signallinjer', 'valförordning', 'vallokalers', 'textmängden', 'partivalsedlar'] 

['mandatfördelnings-', 'risklista', '41976x1008', '31993l0109', 'valmyndighet-', 'förväxlad', 'gistreringsverkets', 'kungörandetidning', 'trehundrationdel', 'röstningsområden'] 

['röstländ', 'valskärmar', 'dubblettröstkort', 'omslags-', 'budrösta', 'tj

['närsbanken', 'förmånsrättstagare', 'tvångsnedsättningen', 'nettoutbetalningar', 'funk-t', 'insättningsfordringar', 'underhandsackordet', 'systemskadliga', 'kornmitten', 'ande/åtagande'] 

['förmögenhetstaxering', 'skattepliktsgränsen', 'skattepliktsgräns', 'samtax', 'förmögenhetsskatteuttag', 'bokföringsvärdet', '333/2003', 'oslobörsens', 'smb-lista', 'ligningstakst'] 

['liebritz', 'bibbe', 'bruttoavkast-', 'ägarklimat', 'ägarklimatet', 'talinkomstskatten', 'skatteplane', 'samhällsekono261', 'vridningarna', 'a-aktien'] 

['privatbostadsrät-', 'bevu41', 'förmögenhetsbeskattats', 'talförsäkringar', 'ålders283', 'tjänstepensionsmodeller', 'itp-planen/itpk', 'pa-91/kåpan', 'skatteplaneringens', 'likformighetsperspektiv'] 

['skattestas', 'hetsbeskatta', 'privatbostadsrätter-', 'lägenhetsregis-', '467–472', 'vatbostadsrätter', 'privatbostadsrättens', 'privatbostadsrätters', 'nadsvärdebaserat', 'värderingsförfa-'] 

['företagskapitalet', 'otc-listorna', 'talmarknad', 'otc-listor', 'diggjo

...

['omprocessuell', 'kontoavstämningens', 'överbetalning', 'delikt', 'tåndet', 'bolagstöm-', 'skadevål-', 'förskottsavdrag', 'aktielagen', 'abgabenordnung'] 

['bördsterminen', 'staltade', 'uppbördsterminen', 'uppbördstermin', 'ålig68', 'uppbördstermi-', 'källskattebelopp', 'gäddede-', 'gäddede-bolaget', 'uppbördstillfälle'] 

['ningsinställelsen', 'betalningsinställelserna', 'ståndsområdet', 'befrielseregeln', 'ansvarsmålen', '9875-', '97/920', 'skattebrottsutredningens', 'darfallen', 'talningsansvarsfrågan'] 

['bakom92', 'betalningsansvarsmålen', '–förvaltningsdomstols', 'företrädaransvarsprocessen', 'bolaget/konkursförvaltaren', 'tefordran', 'betalningsansvarsfrågan', 'tefrågan', 'förlikningsinstitutets', 'inne98'] 

['nehållen', '444–445', 'stadfästelsedomen', 'stadfästelsen', 'rätt–kammarrätt', 'avgiftsmålet', 'betal110', 'ningsansvarsdelen', 'svarsmålen', 'ägare/bolagsman'] 

['älåggas', 'ursprungsförfallodagen', 'månadsavstämning', '-rätt', 'ikraftträ131', 'alternativyrkande', 's

['3–4b', 'prece-', 'swe378', 'ansvarsfriskrivning', 'byggnadsarbetareförbun-', 'skouris', 'jann', 'lenaerts', 'lõhmus', 'schintgen'] 

['löneöverenskommelser', 'månadslöne-', 'stupstocksregeln', 'stupstockslönen', 'förhandlingsmekanism', 'preussen-', '390/99', 'gemenskapsdomstolen', '475/99', '8089'] 

['[123]\ufeffalternativ', '978-91-38-22735-0', 'jämställdhetsdepartemen-', 'byrådirektö-', '/irja', 'hegrelius', 'avdelningsdi-', 'öhrnell', 'avenberg', 'uncitrals'] 

['småkravsprocess', 'förprocessuella', 'tvistemålsförfarande', 'formlöshet', 'geding', 'forliksråd', 'obstruerande', 'utomprocessuell', 'forumfrågor', 'tvisteföremålets'] 

['rättegångsformen', 'tvistlösningsmeka-', 'skyl15', 'likningslösning', 'tvistemålsförfaranden', 'rättegångbalkens', 'snabbrättegångens', 'förlikningsdiskussion', 'tvisternas', 'tvistlösningsmetoder'] 

['district-court', 'of-court', 'sharpened', 'ciliatory', 'diation', 'value-laden', 'insists', 'dispute-resolution', 'concentra-', 'pedient'] 

['tvistlö

['terroristliknande', 'tabuartat', 'räddningskaraktär', 'arbetardemonstration', 'ådalstragedin', 'ådalskom-', 'långrörs', 'sulfitfabrik', 'sympatikonflikter', 'sulfitfabriken'] 

['timglasperspektivet', 'likatoriska', 'speldeltagarna', 'strukturera-', 'spelresultaten', 'positionsindikatorer', 'septemberattackerna', 'radarskärmarna', 'kapar-', 'flygövervakarna'] 

['cbrn-kunnig', 'snabbinsatsresurs', 'cbrn-relaterade', 'sprängatten-', 'cbrn-beredskap', 'nbc-styrka', 'bombskyddsverksamhet', 'bombskyddsverksam-', 'bombskyddsmyndighet', 'bombskyddsteam'] 

['styrningsuppgifter', 'ickepolisiär', 'kontraktspersonal', 'försvarsmakt-', 'befogenhet-', 'terroristattacker-', 'terroristaktörer', 'stödförordningen', 'verk97', 'terroristsammanhang'] 

['deprecating', 'staircase', 'tragic', 'hijacking', 'preventative', '[66]\ufeffsou', 'vesteringsguld', 'guldmaterial', 'tusendelar', 'antiquated'] 

['producentföretags', 'centföretaget', 'missionärsföretag', 'tentföretag', 'sionärsförhållande', 'kommi


['bss-grupperingen', 'utbrytargrupp', 'fredsorga-', '001304-4920', 'fredsarrangemang', 'hetssektioner', 'valsedelsutde-', 'tidningsförsäljare', 'djurrättsaktivist', 'huvudenhetscheferna'] 

['teruppgifterna', '1979-83', 'registreringsföre', 'kommunistdominerade', 'munistövervakning', 'informationsinsamlingens', 'tvi367', 'velsmål', 'avstaliniseringen', 'na/sympatisörerna'] 

['prenumerationsärenden', 'täpptes', 'uppsnappats', '720-6', 'gallring]', 'tele379', 'underrätter-', 'spionerisammanhang', '3023-99', '001310-3148-01'] 

['sabotageverk-', 'vakningsinsatserna', 'mikrofilmkopia', 'rofilmskopia', 'sinnig', 'flugpapper', 'klerks', 'tolkningsföreskrifter', 'ämndens', 'regeringsföreskrifternas'] 

['41/02', 'kerhetsprövning', '1951-95', 'personalkontroll/säkerhetsprövning', 'illo-', 'jala', '407\ufeffbilaga', 'självmordsnivån', 'annorexi', 'bullemi'] 

['stefans', 'identitetsstörningar', 'magpumpning', 'förälrar', 'antideprressiv', 'indianska', 'kortvuxen', 'blåsvart', 'ordsbeteende', 

['lokalanställdas', 'familje70', 'biståndsarbetarens', 'strålningssäkerhet', 'slösningar', '747–749', 'universitetstjänste-', 'avgränsningsproblematik', 'socialförsäkringsarrangemang', 'biståndsarbetares'] 

['sfi-reglerna', 'sö1999', 'fallsrelaterad', 'gästlandet', 'högkvartersavtalen', 'diplomatbeskickningar', 'värdesskattebefrielse', 'not]', 'kvartersavtal', 'skollagsutredningen'] 

['näringsdepartementet]', 'brottmålskonvention', 'traktatfrågor', 'samtals104', 'traktatsbestämmelse', 'rättstillämpade', 'författningssystemets', 'i/12', 'ii/78', 'utvecklings111'] 

['funktionalitetsprincipens', 'havsrättstribunalen', 'heltidsarbetstillfällen/år', 'resediplomati', 'världssekretariat', 'värdlandsrelaterade', 'statsekonomiskt', 'kantonens', 'sjöfartsstad', 'internationaliseringspolitiskt'] 

['universitetstjänsteman', 'privattjänares', 'folbokföringslagen', 'socialavgift-', 'landsavtalets', 'värdlandsavtalets', '[25]\ufeffetiskt', '978-91-38-22788-6', 'universitetsveterinären', 'jeneskog

In [13]:
list1 = sorted(x, key=x.get, reverse=True)
x[list1[0]]

8.1728

In [14]:
granska_ord = Counter(words)

In [15]:
granska_ord['träden']

6

Men hur får man fram när man byter ämne i texten

## Bigrams

In [16]:
# https://stackoverflow.com/questions/43473736/most-common-2-grams-using-python

def bigrams(words):
    bigr = zip(words, words[1:])
    #print (list(bigr))
    counts = Counter(bigr)
    #print(counts)
    print(counts.most_common()[:10])

In [18]:
# https://stackoverflow.com/questions/43473736/most-common-2-grams-using-python

def trigrams(words):
    trigr = zip(words, words[1:], words[2:])
    #print (list(bigr))
    counts = Counter(trigr)
    #print(counts)
    print(counts.most_common()[:10])

In [68]:
bigrams('som om man inte om man skulle'.split())

[(('om', 'man'), 2), (('som', 'om'), 1), (('man', 'inte'), 1), (('inte', 'om'), 1), (('man', 'skulle'), 1)]


In [17]:
bigrams(words)

[(('<COMMA>', 'som'), 466), (('<COMMA>', 'och'), 362), (('<COMMA>', 'att'), 330), (('<COMMA>', '<COMMA>'), 224), (('<COMMA>', 'men'), 190), (('och', '<COMMA>'), 138), (('en', '<COMMA>'), 120), (('<COMMA>', 'så'), 106), (('<COMMA>', 'i'), 99), (('i', '<COMMA>'), 99)]


In [19]:
trigrams(words)

[(('<COMMA>', '<COMMA>', '<COMMA>'), 95), (('<COMMA>', 'att', 'han'), 38), (('<COMMA>', 'och', '<COMMA>'), 31), (('<LEFT_PAREN>', '<RIGHT_PAREN>', '<COMMA>'), 29), (('den', '<COMMA>', 'som'), 26), (('<COMMA>', '<COMMA>', 'och'), 26), (('<COMMA>', 'så', 'att'), 23), (('<COMMA>', 'och', 'då'), 22), (('en', '<COMMA>', 'som'), 22), (('<COMMA>', 'som', 'i'), 21)]


In [25]:
re.sub('<\w*>|<\/\w*>','',text)

'CARL von LINNÈS\n\nLEFNADSMINNEN\n<table o>\n<td c>tecknade af honom sjelf\n\n<td c>*\n\n<td c>med tillägg efter tryckta och otryckta källor\n<td c>af\n<td c>ARVID AHNFELT.\n\n<td c>*\n\n<td c>stockholm\n\noscar l. lamms förlag.\n\n<td c>*\n\n<td c>Pris: 2 Kr. 50 öre.\n\n\nObs omslagets sista sida!\n\n\nIntressanta Nyheter\n\nNyligen utkomna på Oscar L. Lamms förlag\n\nInteriörer ur det literära Stockholmslifvet\n\nunder förra hälften af vårt århundrade.\n\nSamlade och belysta af\n\nARVID AHNFELT.\n\nI.\n\n2 kr. 50 öre.\n\nObs! — — A. har lemnat några högt intressanta bidrag, som står\noss så nära, men som likväl för flertalet är långt mera obekant, än man\nkunde tro — —\n\n— — Med den lätta stil, som alltid utmärker A:s penna, tecknar han\ndessa bilder. — —Boken rekommenderas synnerligen.\n(T. f. V.  st. o. L.)\n\n— — Det är med verkligt nöje vi läst detta häfte — — den lätthet,\nmed hvilken förf. behandlar sitt ämne, bidrager i sin mån att göra \ndetsamma intressant.(C. T.)\n\n—\n\n

In [236]:
# Från https://github.com/udacity/deep-learning/tree/master/embeddings 
def create_lookup_tables(words):
    """
    Create lookup tables for vocabulary
    :param words: Input list of words
    :return: A tuple of dicts.  The first dict....
    """
    word_counts = Counter(words)
    sorted_vocab = sorted(word_counts, key=word_counts.get, reverse=True)
    int_to_vocab = {ii: word for ii, word in enumerate(sorted_vocab)}
    vocab_to_int = {word: ii for ii, word in int_to_vocab.items()}

    return vocab_to_int, int_to_vocab, word_counts

In [237]:
vocab_to_int, int_to_vocab, word_counts = create_lookup_tables(words)
int_words = np.array([vocab_to_int[word] for word in words])

In [154]:
int_words

array([ 3959,   648,  3960, ..., 11034,  1032,  1733])

In [190]:
vocab_to_int['familjeanteckningar']

5299

In [249]:
occs = np.where(int_words == vocab_to_int['standardförfarandena'])

In [250]:
reading_context = 300

In [251]:
text = ' '.join(sample); text

'vestgötaresan <PERIOD> </i> marstrand den juli 1746 <PERIOD> kallades här i den <COMMA> som icke sjelf kan ned i att fisk <COMMA> utan endast är till bland <PERIOD> man med nöje huru denne de andra <COMMA> så snart de fått någon fisk <COMMA> och ej igen att dem måste ut den fisk han och redan <PERIOD> jag har sett med förundran på en <COMMA> som jag flere år haft i <COMMA> att om han fått aldrig så litet mat och någon sedermera litet efter honom <COMMA> har han då strax det han <PERIOD> denna att lätt har skaparen användt att vår <COMMA> ty som ofta mera än de böra <COMMA> så hafva de också väl råd att gifva åt <COMMA> men deremot har naturen likväl så <COMMA> att denne ej allt för mycket får sig <COMMA> hvarför han ock är den af alla <PERIOD> härtill kommer att denne icke är mycket <COMMA> ty under tiden måste <COMMA> då de ej hafva något på <COMMA> och kasta för honom mat <COMMA> hvilken han ock håller till <PERIOD> är mycket <COMMA> så att han alltid tager i luften <COMMA> då den å

In [252]:
occs = occs[0]
occs

array([26903])

In [253]:
# https://stackoverflow.com/questions/2400840/finding-differences-between-elements-of-a-list
dists = [j-i for i, j in zip(occs[:-1], occs[1:])]
dists

[]

In [254]:
def make_chunks(occs, limit):
    b = []
    b.append(occs[0])
    s = []
    for i in range (1, len(occs)) :
        if occs[i] - occs[i-1] > limit:
            b.append(occs[i])
            s.append(occs[i-1])
    s.append(occs[-1])
    return zip(b,s)

In [255]:
chunks = make_chunks(occs, 300)

In [256]:
chunks = list(chunks)

In [257]:
def text_chunks(words, chunks, padding):
    texts = []
    for chunk in chunks:
        text = words[chunk[0]-padding:chunk[1]+padding]
        text = ' '.join(text)
        texts.append(text)
    return texts

In [258]:
t = text_chunks(words, chunks, 5)

In [259]:
t

['för att de generella organisatoriska standardförfarandena skall kunna tillämpas och']